In [1]:
%load_ext nb_black

<IPython.core.display.Javascript object>

In [2]:
import pandas as pd
import urllib
import requests
import regex as re
from bs4 import BeautifulSoup

import gutenberg_cleaner as gclean

import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

from gensim.models import Word2Vec

<IPython.core.display.Javascript object>

In [3]:
# Parameters
book_list = "../data/book_list.csv"

REMOVE_WORDS = ["[deleted]"]

<IPython.core.display.Javascript object>

In [4]:
chapter_regex = re.compile("(I.)[\s\w\\n]*(II).[\s\w\\n]*(III).[\s\w\\n]*")

<IPython.core.display.Javascript object>

In [5]:
# Get list of books and their links
df = pd.read_csv(book_list)

<IPython.core.display.Javascript object>

# Get Text from Web

In [6]:
def clean_paragraphs(par):

    # Replace special characters
    par = par.replace("\n", " ")
    par = par.replace("\\", "")

    # Remove leading whitespace
    par = par.lstrip()

    return par

<IPython.core.display.Javascript object>

In [13]:
X = []
y = []
stop_words = set(stopwords.words("english"))

<IPython.core.display.Javascript object>

In [14]:
for _, row in df.iterrows():
    label = row.get("author")
    target_url = row.get("link")

    # Get text
    soup_html = urllib.request.urlopen(target_url).read()
    text = str(BeautifulSoup(soup_html))
    text_clean = gclean.super_cleaner(text)

    # Separate into paragraphs
    paragraphs = text_clean.split("\n\n")
    paragraphs = [item for item in paragraphs if item not in REMOVE_WORDS]
    paragraphs = [par for par in paragraphs if re.search(chapter_regex, par) is None]

    # Clean paragraphs
    paragraphs = list(map(lambda x: clean_paragraphs(x), paragraphs))

    # Append to data
    X.extend(paragraphs)
    y.extend([label] * len(paragraphs))

<IPython.core.display.Javascript object>

In [360]:
target_url = df["link"][2]

# Request
text = requests.get(target_url).text

# Soup
url = urllib.request.urlopen(target_url)
html = urllib.request.urlopen(target_url).read()
soup = str(BeautifulSoup(html))

<IPython.core.display.Javascript object>

In [361]:
soup

'<html><body><p>The Project Gutenberg EBook of David Copperfield, by Charles Dickens\r\n\r\nThis eBook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  You may copy it, give it away or\r\nre-use it under the terms of the Project Gutenberg License included\r\nwith this eBook or online at www.gutenberg.org\r\n\r\n\r\nTitle: David Copperfield\r\n\r\nAuthor: Charles Dickens\r\n\r\nRelease Date: December, 1996  [Etext #766]\r\nPosting Date: November 24, 2009\r\nLast Updated: September 25, 2016\r\n\r\nLanguage: English\r\n\r\nCharacter set encoding: UTF-8\r\n\r\n*** START OF THIS PROJECT GUTENBERG EBOOK DAVID COPPERFIELD ***\r\n\r\n\r\n\r\n\r\nProduced by Jo Churcher\r\n\r\n\r\n\r\n\r\n\r\nDAVID COPPERFIELD\r\n\r\n\r\nBy Charles Dickens\r\n\r\n\r\n\r\n               AFFECTIONATELY INSCRIBED TO\r\n               THE HON.  Mr. AND Mrs. RICHARD WATSON,\r\n               OF ROCKINGHAM, NORTHAMPTONSHIRE.\r\n\r\n\r\nCONTENTS\r\n\r\n\r\n     I.      I Am 

<IPython.core.display.Javascript object>

In [366]:
text_clean = gclean.super_cleaner(soup)

<IPython.core.display.Javascript object>

In [367]:
text_clean

'[deleted]\n\n[deleted]\n\n[deleted]\n\n[deleted]\n\n[deleted]\n\n[deleted]\n\n[deleted]\n\n[deleted]\n\n[deleted]\n\n[deleted]\n\n\nI do not find it easy to get sufficiently far away from this Book, in\nthe first sensations of having finished it, to refer to it with the\ncomposure which this formal heading would seem to require. My interest\nin it, is so recent and strong; and my mind is so divided between\npleasure and regret--pleasure in the achievement of a long design,\nregret in the separation from many companions--that I am in danger of\nwearying the reader whom I love, with personal confidences, and private\nemotions.\n\nBesides which, all that I could say of the Story, to any purpose, I have\nendeavoured to say in it.\n\nIt would concern the reader little, perhaps, to know, how sorrowfully\nthe pen is laid down at the close of a two-years’ imaginative task; or\nhow an Author feels as if he were dismissing some portion of himself\ninto the shadowy world, when a crowd of the cre

<IPython.core.display.Javascript object>

In [368]:
# Parse text into paragraphs
paragraphs = text_clean.split("\n\n")

# Remove items (e.g., [deleted])
paragraphs = [par for par in paragraphs if par not in REMOVE_WORDS]
paragraphs = [par for par in paragraphs if re.search(chapter_regex, par) is None]

<IPython.core.display.Javascript object>

In [369]:
paragraphs

['\nI do not find it easy to get sufficiently far away from this Book, in\nthe first sensations of having finished it, to refer to it with the\ncomposure which this formal heading would seem to require. My interest\nin it, is so recent and strong; and my mind is so divided between\npleasure and regret--pleasure in the achievement of a long design,\nregret in the separation from many companions--that I am in danger of\nwearying the reader whom I love, with personal confidences, and private\nemotions.',
 'Besides which, all that I could say of the Story, to any purpose, I have\nendeavoured to say in it.',
 'It would concern the reader little, perhaps, to know, how sorrowfully\nthe pen is laid down at the close of a two-years’ imaginative task; or\nhow an Author feels as if he were dismissing some portion of himself\ninto the shadowy world, when a crowd of the creatures of his brain\nare going from him for ever. Yet, I have nothing else to tell; unless,\nindeed, I were to confess (which m

<IPython.core.display.Javascript object>

In [370]:
paragraphs = list(map(lambda x: clean_paragraphs(x), paragraphs))

<IPython.core.display.Javascript object>

In [371]:
paragraphs

['I do not find it easy to get sufficiently far away from this Book, in the first sensations of having finished it, to refer to it with the composure which this formal heading would seem to require. My interest in it, is so recent and strong; and my mind is so divided between pleasure and regret--pleasure in the achievement of a long design, regret in the separation from many companions--that I am in danger of wearying the reader whom I love, with personal confidences, and private emotions.',
 'Besides which, all that I could say of the Story, to any purpose, I have endeavoured to say in it.',
 'It would concern the reader little, perhaps, to know, how sorrowfully the pen is laid down at the close of a two-years’ imaginative task; or how an Author feels as if he were dismissing some portion of himself into the shadowy world, when a crowd of the creatures of his brain are going from him for ever. Yet, I have nothing else to tell; unless, indeed, I were to confess (which might be of less

<IPython.core.display.Javascript object>

In [357]:
res = paragraphs[1]
res

'A Chancery judge once had the kindness to inform me, as one of a company of some hundred and fifty men and women not labouring under any suspicions of lunacy, that the Court of Chancery, though the shining subject of much popular prejudice (at which point I thought the judge\'s eye had a cast in my direction), was almost immaculate. There had been, he admitted, a trivial blemish or so in its rate of progress, but this was exaggerated and had been entirely owing to the "parsimony of the public," which guilty public, it appeared, had been until lately bent in the most determined manner on by no means enlarging the number of Chancery judges appointed--I believe by Richard the Second, but any other king will do as well.'

<IPython.core.display.Javascript object>

In [359]:
new = res.replace("\\", "")
new

'A Chancery judge once had the kindness to inform me, as one of a company of some hundred and fifty men and women not labouring under any suspicions of lunacy, that the Court of Chancery, though the shining subject of much popular prejudice (at which point I thought the judge\'s eye had a cast in my direction), was almost immaculate. There had been, he admitted, a trivial blemish or so in its rate of progress, but this was exaggerated and had been entirely owing to the "parsimony of the public," which guilty public, it appeared, had been until lately bent in the most determined manner on by no means enlarging the number of Chancery judges appointed--I believe by Richard the Second, but any other king will do as well.'

<IPython.core.display.Javascript object>

In [19]:
out_data.groupby("label").count()

text
label                         
Austen, Jane              7607
Christie, Agatha         12354
Dickens, Charles         25037
Dostoyevsky, Fyodor      15421
Hugo, Victor             23405
London, Jack              8340
Stowe, Harriett Beecher  12794
Twain, Mark              10837

<IPython.core.display.Javascript object>

In [18]:
# Create an output set
# out_data = pd.DataFrame({"text": X, "label": y})
# out_data.to_csv("../data/clean_data.csv")

<IPython.core.display.Javascript object>